In [1]:
import os
import sys
import torch
import torchaudio
import numpy as np
from src.CQT_nsgt import CQT_nsgt
import soundfile as sf
import math
import time
torch.set_printoptions(linewidth=2000, threshold=170000)
np.set_printoptions(threshold=sys.maxsize)

In [11]:
#STEREO example
example="/scratch/work/molinee2/projects/ddpm/diffusion_autumn_2022/CQTdiff/test_dir/44100_long/MIDI-Unprocessed_02_R1_2009_03-06_ORIG_MID--AUDIO_02_R1_2009_02_R1_2009_04_WAV.wav"
#example="/scratch/work/molinee2/projects/ddpm/diffusion_autumn_2022/CQTdiff/test_dir/22050_long/MIDI-Unprocessed_02_R1_2009_03-06_ORIG_MID--AUDIO_02_R1_2009_02_R1_2009_04_WAV.wav"
a,fs=sf.read(example)
#a=0.5*(a[...,0]+a[...,1])
#resample=torch.resample()
a=a.transpose()
x=torch.Tensor(a)
x=torchaudio.functional.resample(x, 44100, 22050)

numocts=7
binsoct=64

Ls=88200 # most efficient one
cqt=CQT_nsgt(numocts, binsoct, mode="critical",fs=fs, audio_len=Ls)

/scratch/work/molinee2/projects/ddpm/diffusion_autumn_2022/CQT_pytorch/src/nsgt/nsgfwin.py:66: UserWarning:

Q-factor too high for frequencies 172.27,174.15,176.05,177.97,179.91,181.87,183.86



In [3]:
#MONO example
#example="/scratch/work/molinee2/projects/ddpm/diffusion_autumn_2022/CQTdiff/test_dir/44100_long/MIDI-Unprocessed_02_R1_2009_03-06_ORIG_MID--AUDIO_02_R1_2009_02_R1_2009_04_WAV.wav"
example="/scratch/work/molinee2/projects/ddpm/diffusion_autumn_2022/CQTdiff/test_dir/22050_long/MIDI-Unprocessed_02_R1_2009_03-06_ORIG_MID--AUDIO_02_R1_2009_02_R1_2009_04_WAV.wav"
a,fs=sf.read(example)
#a=0.5*(a[...,0]+a[...,1])
#a=a.transpose()
#x=torch.Tensor(a)
#x=torchaudio.functional.resample(x, 44100, 22050)
#x.shape
x=torch.Tensor(a).unsqueeze(0)

numocts=7
binsoct=64

Ls=88200 # most efficient one
cqt=CQT_nsgt(numocts, binsoct, mode="oct",fs=fs, audio_len=Ls)


/scratch/work/molinee2/projects/ddpm/diffusion_autumn_2022/CQT_pytorch/src/nsgt/nsgfwin.py:66: UserWarning: Q-factor too high for frequencies 86.13,87.07,88.02,88.98,89.95,90.94,91.93
  warn("Q-factor too high for frequencies %s"%",".join("%.2f"%fi for fi in f[q >= qneeded]))


/scratch/work/molinee2/projects/ddpm/diffusion_autumn_2022/CQT_pytorch/src/nsgt/nsgfwin.py:66: UserWarning: Q-factor too high for frequencies 86.13,87.07,88.02,88.98,89.95,90.94,91.93
  warn("Q-factor too high for frequencies %s"%",".join("%.2f"%fi for fi in f[q >= qneeded]))


In [12]:
x=x[:,0:Ls]
start=time.time()
#X=forward(x)
X=cqt.fwd(x)
end=time.time()
print(end-start)

0.08789658546447754


In [13]:
X[0].shape

torch.Size([1, 2, 1, 689])

In [14]:
start=time.time()
#xrec=backward(X)
xrec=cqt.bwd(X)
end=time.time()
print(end-start)

0.2221384048461914


In [8]:
xrec.shape

torch.Size([2, 88200])

In [15]:
A=torch.stft(x[0], 1024)
Arec=torch.stft(xrec[0], 1024)
error=A[:,:,:]-Arec[:,:,:]
Error=torch.sqrt(error[...,1]**2+error[...,0]**2).squeeze(0)
import plotly.express as px
px.imshow(10*torch.log10(Error))


In [16]:
A=torch.stft(x[1], 1024)
Arec=torch.stft(xrec[1], 1024)
error=A[:,:,:]-Arec[:,:,:]
Error=torch.sqrt(error[...,1]**2+error[...,0]**2).squeeze(0)
import plotly.express as px
px.imshow(10*torch.log10(Error))

NameError: name 'ipd' is not defined

In [11]:
import IPython.display as ipd
ipd.Audio(xrec, rate=22050, autoplay=True) # load a NumPy array

In [12]:
ipd.Audio(x, rate=22050, autoplay=True) # load a NumPy array